In [5]:
import os

import pandas as pd
import datetime
import numpy as np

from tqdm import tqdm

from indicators_v2 import *
from signals_v2 import *
from dealManager import *
from trandeVoter import *
from riskManager import *
import pickle

In [6]:
df_candle = pd.read_csv("../data/EURUSD_price_candlestick.csv")
df_candle.rename(columns={'timestamp': 'date'}, inplace=True)
df_candle

date     open    close     high      low
0      2020-09-01 03:00:00+03:00  1.19370  1.19388  1.19391  1.19368
1      2020-09-01 03:00:05+03:00  1.19387  1.19388  1.19391  1.19383
2      2020-09-01 03:00:10+03:00  1.19387  1.19384  1.19389  1.19382
3      2020-09-01 03:00:15+03:00  1.19384  1.19384  1.19386  1.19382
4      2020-09-01 03:00:20+03:00  1.19387  1.19390  1.19391  1.19383
...                          ...      ...      ...      ...      ...
99995  2020-09-06 21:52:55+03:00  1.18382  1.18382  1.18393  1.18371
99996  2020-09-06 21:53:00+03:00  1.18382  1.18382  1.18393  1.18371
99997  2020-09-06 21:53:05+03:00  1.18382  1.18382  1.18393  1.18371
99998  2020-09-06 21:53:10+03:00  1.18382  1.18382  1.18393  1.18371
99999  2020-09-06 21:53:15+03:00  1.18382  1.18382  1.18393  1.18371

[100000 rows x 5 columns]

In [7]:
df_candle['close']

0        1.19388
1        1.19388
2        1.19384
3        1.19384
4        1.19390
          ...   
99995    1.18382
99996    1.18382
99997    1.18382
99998    1.18382
99999    1.18382
Name: close, Length: 100000, dtype: float64

In [8]:
class decsionManager:
    '''
sigAgrReq = {
    'sig_BB':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':30,'valueType':'close','kDev':2.5}
            }            
        }
    },
    'sig_BB_2':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':30,'valueType':'close','kDev':2}
            }            
        }
    }
}

sigAgrData = {
    'sig_BB':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    },
    'sig_BB_2':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    }    
}


sigAgrRetroTemplate = {
    'sig_BB':{
        'signalData': None,
        'indicatorData' :{'ind_BB': None}
    },
    'sig_BB_2':{
        'signalData': None,
        'indicatorData' :{'ind_BB': None}
    }     
}    
    
    
    
    
    
    
    '''
    
    
    
    
    def __init__(self,name, sigDict: dict):
        self.RM = riskManager()
        self.DM = DealManager()
        self.TV = trandeVoter(name)
        self.SA = signalsAgrigator(sigDict)
        self.sigDict = sigDict
        
        
    def getOnlineAns(self, signalsAns: dict, price: float) -> dict:
        probabilityDecsion = self.TV.getDecisionBySignals(self.getSignalsAns(signalsAns))
        RMD = self.RM.getDecision(probabilityDecision=probabilityDecsion, price=price, deals = self.DM.deals)
        return RMD
        
    def getSignalsAns(self, signalsDataDict: dict) -> dict:
        return self.SA.getAns(signalsDataDict)
    
    def getRightAns(self,value_1, value_2):
        
        ans=''
        
        if value_1 > value_2:
            ans = 'down'
        elif value_1 < value_2:
            ans = 'up'
        else:
            ans = 'none'
        
        return ans
        
    def getRetroTrendAns(self, retroTemplateDict: dict, data: pd.DataFrame(), window: int) -> list:
        
        reqSig={} 
        ans = {
            'signalsAns':[],
            'rightAns':[]
            
        }
        target = ''
        
        
        for k in tqdm(range(data.shape[0]-window-1)):
            for i in retroTemplateDict.keys():
                reqSig[i] = {'signalData': data[k:k+window], 'indicatorData':{}}
                target = self.SA.signals[i].params['target']
                for j in retroTemplateDict[i]['indicatorData'].keys():
                    reqSig[i]['indicatorData'][j] = data[k:k+window]
                    
            sigAns = self.getSignalsAns(reqSig)
            rightAns = self.getRightAns(data[target][k], data[target][k+1])

            ans['signalsAns'].append(sigAns)
            ans['rightAns'].append(rightAns)

        return ans
 

    def generateMatrixProbabilityFromDict(self, dictSignals: dict) -> dict:
        self.TV.createMatrixAmounts(dictSignals['signalsAns'][0].keys())
        for i in range(len(dictSignals['signalsAns'])):
            self.TV.setDecisionBySignals(signalDecisions = dictSignals['signalsAns'][i],
                                        trande = dictSignals['rightAns'][i])
        self.TV.generateMatrixProbability()
        
    def createDump(self,postfix='') -> str:
        dataDict = {
            'RM':self.RM,
            'DM':self.DM,
            'TV':self.TV,
            'SA':self.SA,
            'sigDict':self.sigDict
        }
        fileName='data_'+postfix+'.pickle'
        with open(fileName, 'wb') as f:
            pickle.dump(dataDict, f)
            
        return os.path.abspath(fileName)
    
    def loadDump(self,path: str) -> None:
        
        with open(path, 'rb') as f:
            dataDict = pickle.load(f)
        
        self.RM = dataDict['RM']
        self.DM = dataDict['DM']
        self.TV = dataDict['TV']
        self.SA = dataDict['SA']
        self.sigDict = dataDict['sigDict']

In [9]:
sigAgrReq = {
    'sig_BB':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':30,'valueType':'close','kDev':2.5}
            }            
        }
    },
    'sig_BB_2':{
        'className':sig_BB,
        'params':{'source':'close','target':'close'},
        'indicators':{
            'ind_BB':{
                'className':ind_BB,
                'params':{'MeanType':'SMA','window':30,'valueType':'close','kDev':2}
            }            
        }
    }
}

sigAgrData = {
    'sig_BB':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    },
    'sig_BB_2':{
        'signalData': df_candle[990:1000],
        'indicatorData' :{'ind_BB': df_candle[:1000]}
    }    
}


sigAgrRetroTemplate = {
    'sig_BB':{
        'signalData': None,
        'indicatorData' :{'ind_BB': None}
    },
    'sig_BB_2':{
        'signalData': None,
        'indicatorData' :{'ind_BB': None}
    }     
}

In [10]:
test = decsionManager('Pipa', sigAgrReq)

In [11]:
test.__dict__

{'RM': <riskManager.riskManager at 0x7f8e4947f390>,
 'DM': <dealManager.DealManager at 0x7f8e76bda610>,
 'TV': <trandeVoter.trandeVoter at 0x7f8e973b3ed0>,
 'SA': <signals_v2.signalsAgrigator at 0x7f8e4948d410>,
 'sigDict': {'sig_BB': {'className': signals_v2.sig_BB,
   'params': {'source': 'close', 'target': 'close'},
   'indicators': {'ind_BB': {'className': indicators_v2.ind_BB,
     'params': {'MeanType': 'SMA',
      'window': 30,
      'valueType': 'close',
      'kDev': 2.5}}}},
  'sig_BB_2': {'className': signals_v2.sig_BB,
   'params': {'source': 'close', 'target': 'close'},
   'indicators': {'ind_BB': {'className': indicators_v2.ind_BB,
     'params': {'MeanType': 'SMA',
      'window': 30,
      'valueType': 'close',
      'kDev': 2}}}}}}

In [12]:
test.TV.__dict__

{'name': 'Pipa',
 'trandeValuesList': ['up', 'none', 'down'],
 'matrixAmounts': None,
 'keysMatrixAmounts': None,
 'matrixProbability': None}

In [13]:
test.SA.signals['sig_BB'].params['target']

'close'

In [14]:
test.getSignalsAns(sigAgrData)

{'sig_BB': 'none', 'sig_BB_2': 'down'}

In [15]:
#test.loadDump('C:\\Users\\Redsandy\\PyProj\\Trade\\MVP\\data_pupa.pickle')

In [16]:
uuu = test.getRetroTrendAns(sigAgrRetroTemplate,df_candle[:5000],40)
uuu

100%|██████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 4959/4959 [00:14<00:00, 339.27it/s]


{'signalsAns': [{'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'down'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none', 'sig_BB_2': 'none'},
  {'sig_BB': 'none',

In [17]:
test.generateMatrixProbabilityFromDict(uuu)

/home/parf/projects/marketTrade/MVP/trandeVoter.py:48: RuntimeWarning: invalid value encountered in scalar divide
  self.matrixProbability.iloc[i]['up'] = (self.matrixAmounts.iloc[i]['up'] / rowSum)
/home/parf/projects/marketTrade/MVP/trandeVoter.py:49: RuntimeWarning: invalid value encountered in scalar divide
  self.matrixProbability.iloc[i]['none'] = self.matrixAmounts.iloc[i]['none'] / rowSum
/home/parf/projects/marketTrade/MVP/trandeVoter.py:50: RuntimeWarning: invalid value encountered in scalar divide
  self.matrixProbability.iloc[i]['down'] = self.matrixAmounts.iloc[i]['down'] / rowSum


In [18]:
test.TV.__dict__

{'name': 'Pipa',
 'trandeValuesList': ['up', 'none', 'down'],
 'matrixAmounts':                    up  none  down
 sig_BB sig_BB_2                  
 up     up          31    35    32
        none         0     0     0
        down         0     0     0
 none   up          61    51    60
        none      1504  1333  1529
        down        67    57    85
 down   up           0     0     0
        none         0     0     0
        down        35    41    38,
 'keysMatrixAmounts': ['sig_BB', 'sig_BB_2'],
 'matrixProbability':                        up      none      down
 sig_BB sig_BB_2                              
 up     up        0.316327  0.357143  0.326531
        none           NaN       NaN       NaN
        down           NaN       NaN       NaN
 none   up        0.354651  0.296512  0.348837
        none      0.344480  0.305314  0.350206
        down      0.320574  0.272727  0.406699
 down   up             NaN       NaN       NaN
        none           NaN       NaN       Na

In [19]:
test.getOnlineAns(sigAgrData, 0.0)

{'decision': 'none'}

In [20]:
(test.DM.deals).shape

(0, 3)

In [21]:
test.createDump('pupa')

'/home/parf/projects/marketTrade/MVP/data_pupa.pickle'

In [22]:
with open('C:\\Users\\Redsandy\\PyProj\\Trade\\MVP\\data_pupa.pickle', 'rb') as f:
    data_new = pickle.load(f)
data_new

FileNotFoundError: [Errno 2] No such file or directory: 'C:\\Users\\Redsandy\\PyProj\\Trade\\MVP\\data_pupa.pickle'